In [1]:
import __init__
from src.utilities import train_test_validation_splits, \
                            prepare_train_test_val_seqs_by_batches, \
                            tensor2dataloader, load_full_meltome_FLIP_db, \
                            seek_UniprotID_association_Meltome_prots
import pandas as pd
import numpy as np
    
path_meltome = '../datasets/FLIP/splits/meltome/splits/mixed_split.csv'
complete_meltome_db = '../datasets/FLIP/splits/meltome/full_dataset_sequences.fasta'

full_meltome_db = load_full_meltome_FLIP_db(complete_meltome_db)

splits_meltome = pd.read_csv(path_meltome, sep=',')
split_meltome = splits_meltome[splits_meltome['sequence'].str.len()>= 50]
train, val, test = train_test_validation_splits(splits_meltome)
train = seek_UniprotID_association_Meltome_prots(train, full_meltome_db)
test = seek_UniprotID_association_Meltome_prots(test, full_meltome_db)
val = seek_UniprotID_association_Meltome_prots(val, full_meltome_db)
#print(train)
print("Done")



#ff=full_meltome_db[full_meltome_db['sequence'].isin(train['sequence'])]

/z/home/sgal/miniconda3/envs/thermoPML/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Done


In [2]:
import profet
from profet import Fetcher
from profet import alphafold
from profet import pdb
from tqdm.auto import tqdm

structuredir = '../datasets/Structures/'
meltome_struct_dir_labels = '../datasets/'


import requests, sys, json

WEBSITE_API = 'https://rest.uniprot.org/'
PROTEINS_API = 'https://www.ebi.ac.uk/proteins/api'
EXAMPLE_ID = 'A0A023T4K3'
EXAMPLE_ID2 = 'A0A0K2H650'#'X02469'

def get_url(url, **kwargs):
    response = requests.get(url,**kwargs)
      
    if not response.ok:
        #print(response.text)
        response.raise_for_status()
        #sys.exit()
        
    return response

# convert Uniprot accessions to uniprot id or primaryaccession to consume
def get_equivalence_UniprotID(WEBSITE_API, ID):
    r = get_url(f"{WEBSITE_API}/uniprotkb/{ID}")
    output = r.json()['primaryAccession']
    return output


def download_UniprotID_Alphafold_Structures(df, tmpdir, label_dir, label_name):
        
    #ONLY_ALPHAFOLD = "F4HvG8"
    #ONLY_PDB = "7U6Q"
    import io
    from contextlib import redirect_stdout
    
    WEBSITE_API = 'https://rest.uniprot.org/'
    PROTEINS_API = 'https://www.ebi.ac.uk/proteins/api'
    
    fetcher = Fetcher()
    fetcher.set_directory(str(tmpdir))
    fetcher.set_default_db("alphafold")
    Uniprot_ID_list =df.protein_id.tolist()
    

    open(label_dir+label_name+'.txt', "a").write("Original_ID\tUniprot_ID\tStructure_Alphafold\tSource\n")
    
    for data in tqdm(Uniprot_ID_list):
        Uniprot_ID = get_equivalence_UniprotID(WEBSITE_API, data)
        f = io.StringIO()

        try:
            with redirect_stdout(f):
                filename, _ = fetcher.get_file(Uniprot_ID, filesave=True, db='alphafold')
                out = f.getvalue().split('\n')[-2].split(':')[1].strip()
                open(label_dir+label_name+'.txt', "a").write(data+'\t'+Uniprot_ID+'\t'+filename+'\t'+out+'\n')
        except:
            open(label_dir+label_name+'.txt', "a").write(data+'\t'+Uniprot_ID+'\t'+'No structure available\tNA'+'\n')
    

download_UniprotID_Alphafold_Structures(train, structuredir, meltome_struct_dir_labels, 'Meltome_Splits_FLIPS_train')
download_UniprotID_Alphafold_Structures(test, structuredir, meltome_struct_dir_labels, 'Meltome_Splits_FLIPS_test')
download_UniprotID_Alphafold_Structures(val, structuredir, meltome_struct_dir_labels, 'Meltome_Splits_FLIPS_val')




  0%|          | 0/22335 [00:00<?, ?it/s]

  0%|          | 1/22335 [00:00<4:02:52,  1.53it/s]

  0%|          | 2/22335 [00:01<3:37:32,  1.71it/s]

  0%|          | 3/22335 [00:01<3:33:06,  1.75it/s]

  0%|          | 4/22335 [00:02<3:26:06,  1.81it/s]

...

100%|█████████▉| 2479/2482 [28:27<00:02,  1.39it/s]

100%|█████████▉| 2480/2482 [28:27<00:01,  1.39it/s]

100%|█████████▉| 2481/2482 [28:28<00:00,  1.43it/s]

100%|██████████| 2482/2482 [28:29<00:00,  1.47it/s]

100%|██████████| 2482/2482 [28:29<00:00,  1.45it/s]

In [3]:
'''
try:
    import py3Dmol

    def view_pdb(fpath, chain_id):
        with open(fpath) as ifile:
            system = "".join([x for x in ifile])

        view = py3Dmol.view(width=600, height=400)
        view.addModelsAsFrames(system)
        view.setStyle({'model': -1, 'chain': chain_id}, {"cartoon": {'color': 'spectrum'}})
        view.zoomTo()
        view.show()

except ImportError:
    def view_pdb(fpath, chain_id):
        print("Install py3Dmol to visualize, or use pymol")
'''
#view_pdb(filename , 'B')
#view_pdb(filename2 , 'A')


'\ntry:\n    import py3Dmol\n\n    def view_pdb(fpath, chain_id):\n        with open(fpath) as ifile:\n            system = "".join([x for x in ifile])\n\n        view = py3Dmol.view(width=600, height=400)\n        view.addModelsAsFrames(system)\n        view.setStyle({\'model\': -1, \'chain\': chain_id}, {"cartoon": {\'color\': \'spectrum\'}})\n        view.zoomTo()\n        view.show()\n\nexcept ImportError:\n    def view_pdb(fpath, chain_id):\n        print("Install py3Dmol to visualize, or use pymol")\n'

In [4]:
'''
import torch
import torch_geometric
import torch_sparse
from torch_geometric.nn import MessagePassing

import esm
model, alphabet = esm.pretrained.esm_if1_gvp4_t16_142M_UR50()
model = model.eval()
'''


'\nimport torch\nimport torch_geometric\nimport torch_sparse\nfrom torch_geometric.nn import MessagePassing\n\nimport esm\nmodel, alphabet = esm.pretrained.esm_if1_gvp4_t16_142M_UR50()\nmodel = model.eval()\n'

In [5]:
'''
!wget https://files.rcsb.org/download/5YH2.cif -P ../datasets/    # save this to the data folder in colab

fpath = '../datasets/5YH2.cif' # .pdb format is also acceptable
chain_id = 'C'
structure = esm.inverse_folding.util.load_structure(fpath, chain_id)
coords, native_seq = esm.inverse_folding.util.extract_coords_from_structure(structure)
print('Native sequence:')
print(native_seq)
print(coords)

rep = esm.inverse_folding.util.get_encoder_output(model, alphabet, coords)
print(rep)
print(rep.shape)
'''

"\n!wget https://files.rcsb.org/download/5YH2.cif -P ../datasets/    # save this to the data folder in colab\n\nfpath = '../datasets/5YH2.cif' # .pdb format is also acceptable\nchain_id = 'C'\nstructure = esm.inverse_folding.util.load_structure(fpath, chain_id)\ncoords, native_seq = esm.inverse_folding.util.extract_coords_from_structure(structure)\nprint('Native sequence:')\nprint(native_seq)\nprint(coords)\n\nrep = esm.inverse_folding.util.get_encoder_output(model, alphabet, coords)\nprint(rep)\nprint(rep.shape)\n"